In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
from pathlib import Path

In [2]:
MAIN_DIR = Path(".").absolute()
BASEBALL_DIR = MAIN_DIR / "baseball_data"
POLIT_DIR = MAIN_DIR / "political_data"

In [3]:
teams_df = pd.read_csv(BASEBALL_DIR / "core" / "Teams.csv")
players_df = pd.read_csv(BASEBALL_DIR / "core" / "People.csv")
batting_df = pd.read_csv(BASEBALL_DIR / "core" / "Batting.csv")
pitching_df = pd.read_csv(BASEBALL_DIR / "core" / "Pitching.csv")
appearances_df = pd.read_csv(BASEBALL_DIR / "core" / "Appearances.csv")
batting_advanced_df = pd.read_csv(BASEBALL_DIR / 'advanced' / 'batting_advanced.csv')
pitching_advanced_df = pd.read_csv(BASEBALL_DIR / 'advanced' / 'pitching_advanced.csv')

In [4]:
batting_df = batting_df[batting_df["yearID"] >= 1899]

In [5]:
batting_df

playerID  yearID  stint teamID lgID    G   AB   R    H  2B  ...  \
7566    anderjo01    1899      1    BRO   NL  117  439  65  118  18  ...   
7567    atherch01    1899      1    WAS   NL   65  242  28   60   5  ...   
7568    baileha01    1899      1    BSN   NL   12   34   3    8   2  ...   
7569    bakerki01    1899      1    WAS   NL   12   19   1    3   0  ...   
7570    barreji01    1899      1    CIN   NL   26   92  30   34   2  ...   
...           ...     ...    ...    ...  ...  ...  ...  ..  ...  ..  ...   
110490  zimmejo02    2021      1    MIL   NL    2    1   0    0   0  ...   
110491  zimmeky01    2021      1    KCA   AL   52    0   0    0   0  ...   
110492  zimmery01    2021      1    WAS   NL  110  255  27   62  16  ...   
110493  zuberty01    2021      1    KCA   AL   31    1   0    0   0  ...   
110494  zuninmi01    2021      1    TBA   AL  109  333  64   72  11  ...   

         RBI    SB   CS  BB     SO  IBB  HBP   SH   SF  GIDP  
7566    92.0  25.0  NaN  27   24.0  NaN  4.0  2.0  NaN   NaN  
7567    23.0   2.0  NaN  21   26.0  NaN  2.0  4.0  NaN   NaN  
7568     2.0   0.0  NaN   2    3.0  NaN  1.0  0.0  NaN   NaN  
7569     1.0   0.0  NaN   1    6.0  NaN  0.0  0.0  NaN   NaN  
7570    10.0   4.0  NaN  18    7.0  NaN  1.0  3.0  NaN   NaN  
...      ...   ...  ...  ..    ...  ...  ...  ...  ...   ...  
110490   0.0   0.0  0.0   0    1.0  0.0  0.0  0.0  0.0   0.0  
110491   0.0   0.0  0.0   0    0.0  0.0  0.0  0.0  0.0   0.0  
110492  46.0   0.0  0.0  16   77.0  0.0  0.0  0.0  2.0   9.0  
110493   0.0   0.0  0.0   0    1.0  0.0  0.0  0.0  0.0   0.0  
110494  62.0   0.0  0.0  34  132.0  0.0  7.0  0.0  1.0   7.0  

[102929 rows x 22 columns]

In [6]:
teams_df["minAB"] = 3.1 * teams_df['G']

In [7]:
batting_heavy_min = pd.merge(batting_df, teams_df[['minAB', 'yearID', 'teamID']], on=['yearID', 'teamID'])

In [8]:
batting_heavy_min["PA"] = batting_heavy_min[["AB", "HBP", "BB", "SF", "SH"]].sum(axis=1, skipna=True)

In [9]:
batting_heavy_min = batting_heavy_min[batting_heavy_min["minAB"] < batting_heavy_min["PA"]]

In [10]:
batting_heavy_data = pd.merge(batting_heavy_min, players_df, on=["playerID"])
batting_heavy_data["fullName"] = batting_heavy_data["nameFirst"] + " " + batting_heavy_data["nameLast"]

In [11]:
batting_heavy_advanced = pd.merge(batting_heavy_data,batting_advanced_df.drop("G", axis=1), on=['yearID','bbrefID'])

In [12]:
batting_heavy_advanced_final = batting_heavy_advanced[['playerID', 'bbrefID', 'yearID', 'fullName', 'teamID', 'birthState', 'birthCountry', 'G','AB', 'R', 'H', '2B', '3B', 'HR', 'RBI', 'SB', 'CS', 'BB', 'SO', 'HBP', 'SH', 'SF', 'WAR', 'oWAR', 'dWAR']]

In [13]:
batting_heavy_advanced_final

playerID    bbrefID  yearID           fullName teamID birthState  \
0      anderjo01  anderjo01    1899      John Anderson    BRO        NaN   
1      anderjo01  anderjo01    1901      John Anderson    MLA        NaN   
2      anderjo01  anderjo01    1902      John Anderson    SLA        NaN   
3      anderjo01  anderjo01    1903      John Anderson    SLA        NaN   
4      anderjo01  anderjo01    1904      John Anderson    NYA        NaN   
...          ...        ...     ...                ...    ...        ...   
12251   lowena01   lowena01    2021     Nathaniel Lowe    TEX         VA   
12252  francty01  francty01    2021          Ty France    SEA         CA   
12253  hernaen02  hernaen02    2021  Enrique Hernandez    BOS        NaN   
12254  renfrhu01  renfrhu01    2021     Hunter Renfroe    BOS         MS   
12255  carlsdy01  carlsdy01    2021      Dylan Carlson    SLN         CA   

      birthCountry    G   AB   R  ...    SB   CS  BB     SO   HBP    SH   SF  \
0           Norway  117  439  65  ...  25.0  NaN  27   24.0   4.0   2.0  NaN   
1           Norway  138  576  90  ...  35.0  NaN  24   21.0   3.0   4.0  NaN   
2           Norway  126  524  60  ...  15.0  NaN  21    9.0   3.0   3.0  NaN   
3           Norway  138  550  65  ...  16.0  NaN  23   39.0   0.0   4.0  NaN   
4           Norway  143  558  62  ...  20.0  NaN  23   37.0   6.0  11.0  NaN   
...            ...  ...  ...  ..  ...   ...  ...  ..    ...   ...   ...  ...   
12251          USA  157  557  75  ...   8.0  0.0  80  162.0   2.0   0.0  3.0   
12252          USA  152  571  85  ...   0.0  0.0  46  106.0  27.0   0.0  6.0   
12253         P.R.  134  508  84  ...   1.0  0.0  61  110.0   9.0   0.0  7.0   
12254          USA  144  521  89  ...   1.0  2.0  44  130.0   1.0   0.0  6.0   
12255          USA  149  542  79  ...   2.0  1.0  57  152.0  11.0   1.0  8.0   

       WAR  oWAR  dWAR  
0      0.6   0.4  -0.2  
1      4.4   4.3  -0.2  
2      0.9   1.3  -0.6  
3      3.3   2.5   0.4  
4      3.2   2.8  -0.3  
...    ...   ...   ...  
12251  2.4   2.6  -1.1  
12252  4.3   4.1  -0.5  
12253  4.9   3.2   2.1  
12254  2.3   2.3  -0.5  
12255  3.3   3.2  -0.2  

[12256 rows x 25 columns]

In [14]:
corrMatrix = batting_heavy_advanced_final.corr()
px.imshow(corrMatrix, text_auto=True, aspect='auto', zmax=1, zmin=-1, color_continuous_scale=px.colors.diverging.Fall)

Pitch

In [15]:
pitching_df = pitching_df[pitching_df["yearID"] >= 1899]
teams_df["minOUT"] = teams_df["G"] * 3
pitching_min = pd.merge(pitching_df, teams_df[['minOUT', 'yearID', 'teamID']], on=['yearID', 'teamID'])
pitching_min = pitching_min[pitching_min["minOUT"] < pitching_min["IPouts"]]

In [16]:
pitching_full = pd.merge(pitching_min, players_df, on=["playerID"])
pitching_full["fullName"] = pitching_full["nameFirst"] + " " + pitching_full["nameLast"]

In [17]:
pitching_full

playerID  yearID  stint teamID lgID   W   L   G  GS  CG  ...  \
0     lewiste01    1899      1    BSN   NL  17  11  29  25  23  ...   
1     lewiste01    1900      1    BSN   NL  13  12  30  22  19  ...   
2     lewiste01    1901      1    BOS   AL  16  17  39  34  31  ...   
3     nichoki01    1899      1    BSN   NL  21  19  42  37  37  ...   
4     nichoki01    1900      1    BSN   NL  13  16  29  27  25  ...   
...         ...     ...    ...    ...  ...  ..  ..  ..  ..  ..  ...   
8547  uriasju01    2021      1    LAN   NL  20   3  32  32   0  ...   
8548  lylesjo01    2021      1    TEX   AL  10  13  32  30   0  ...   
8549  burneco01    2021      1    MIL   NL  11   5  28  28   0  ...   
8550  flexech01    2021      1    SEA   AL  14   6  31  31   0  ...   
8551  ceasedy01    2021      1    CHA   AL  13   7  32  32   1  ...   

             nameGiven  weight  height  bats  throws       debut   finalGame  \
0        Edward Morgan   158.0    70.0     R       R  1896-07-06  1901-09-26   
1        Edward Morgan   158.0    70.0     R       R  1896-07-06  1901-09-26   
2        Edward Morgan   158.0    70.0     R       R  1896-07-06  1901-09-26   
3     Charles Augustus   175.0    70.0     B       R  1890-04-23  1906-05-18   
4     Charles Augustus   175.0    70.0     B       R  1890-04-23  1906-05-18   
...                ...     ...     ...   ...     ...         ...         ...   
8547       Julio Cesar   225.0    72.0     L       L  2016-05-27  2021-10-02   
8548     Jordan Horton   230.0    77.0     R       R  2011-05-31  2021-10-02   
8549      Corbin Brian   225.0    75.0     R       R  2018-07-10  2021-10-02   
8550  Christopher John   250.0    75.0     R       R  2017-07-27  2021-10-02   
8551      Dylan Edward   195.0    74.0     R       R  2019-07-03  2021-10-03   

       retroID    bbrefID       fullName  
0     lewit101  lewiste01      Ted Lewis  
1     lewit101  lewiste01      Ted Lewis  
2     lewit101  lewiste01      Ted Lewis  
3     nichk101  nichoki01    Kid Nichols  
4     nichk101  nichoki01    Kid Nichols  
...        ...        ...            ...  
8547  uriaj001  uriasju01    Julio Urias  
8548  lylej001  lylesjo01   Jordan Lyles  
8549  burnc002  burneco01  Corbin Burnes  
8550  flexc001  flexech01   Chris Flexen  
8551  ceasd001  ceasedy01    Dylan Cease  

[8552 rows x 55 columns]

In [18]:
pitching_full_advanced = pd.merge(pitching_full,pitching_advanced_df.drop(['G','GS'], axis=1), on=['yearID','bbrefID'])
pitching_full_advanced

playerID  yearID  stint teamID lgID   W   L   G  GS  CG  ...  WAA  \
0     lewiste01    1899      1    BSN   NL  17  11  29  25  23  ...  1.6   
1     lewiste01    1900      1    BSN   NL  13  12  30  22  19  ...  0.8   
2     lewiste01    1901      1    BOS   AL  16  17  39  34  31  ...  0.1   
3     nichoki01    1899      1    BSN   NL  21  19  42  37  37  ...  4.3   
4     nichoki01    1900      1    BSN   NL  13  16  29  27  25  ...  2.8   
...         ...     ...    ...    ...  ...  ..  ..  ..  ..  ..  ...  ...   
8733  uriasju01    2021      1    LAN   NL  20   3  32  32   0  ...  2.8   
8734  lylesjo01    2021      1    TEX   AL  10  13  32  30   0  ... -1.6   
8735  burneco01    2021      1    MIL   NL  11   5  28  28   0  ...  4.1   
8736  flexech01    2021      1    SEA   AL  14   6  31  31   0  ...  1.9   
8737  ceasedy01    2021      1    CHA   AL  13   7  32  32   1  ...  1.5   

      gmLI  WAAadj  WAR   RAR  waaWL%  162WL%      Salary           Awards  \
0     1.00    -0.2  3.6  37.0   0.555   0.510         NaN              NaN   
1     1.00    -0.1  2.7  28.0   0.527   0.505         NaN              NaN   
2     1.00    -0.2  3.2  40.0   0.504   0.501         NaN              NaN   
3     1.00    -0.4  7.3  74.0   0.603   0.527      $3,000              NaN   
4     1.00    -0.2  4.8  50.0   0.596   0.517         NaN              NaN   
...    ...     ...  ...   ...     ...     ...         ...              ...   
8733   NaN    -0.2  4.4  43.0   0.588   0.517  $3,600,000            CYA-7   
8734  0.55    -0.1 -0.1   2.0   0.449   0.490  $8,000,000              NaN   
8735   NaN    -0.1  5.6  52.0   0.648   0.526         NaN  AS,CYA-1,MVP-15   
8736   NaN    -0.1  3.5  37.0   0.562   0.512  $1,700,000              NaN   
8737   NaN    -0.1  2.9  31.0   0.546   0.509         NaN              NaN   

      RA9extras  
0           NaN  
1           NaN  
2           NaN  
3           NaN  
4           NaN  
...         ...  
8733        0.0  
8734        0.0  
8735        0.0  
8736        0.0  
8737        0.0  

[8738 rows x 77 columns]

In [19]:
pitching_full_advanced_final = pitching_full_advanced[['playerID', 'bbrefID', 'yearID', 'fullName', 'teamID', 'birthState', 'birthCountry', 'W', 'GS', 'G', 'SV', 'ER', 'SO', 'BB', 'ERA', 'BAOpp', 'WP', 'HR', 'gmLI', 'WAR']]

In [20]:
pitching_full_advanced_final

playerID    bbrefID  yearID       fullName teamID birthState  \
0     lewiste01  lewiste01    1899      Ted Lewis    BSN      Powys   
1     lewiste01  lewiste01    1900      Ted Lewis    BSN      Powys   
2     lewiste01  lewiste01    1901      Ted Lewis    BOS      Powys   
3     nichoki01  nichoki01    1899    Kid Nichols    BSN         WI   
4     nichoki01  nichoki01    1900    Kid Nichols    BSN         WI   
...         ...        ...     ...            ...    ...        ...   
8733  uriasju01  uriasju01    2021    Julio Urias    LAN    Sinaloa   
8734  lylesjo01  lylesjo01    2021   Jordan Lyles    TEX         SC   
8735  burneco01  burneco01    2021  Corbin Burnes    MIL         CA   
8736  flexech01  flexech01    2021   Chris Flexen    SEA         CA   
8737  ceasedy01  ceasedy01    2021    Dylan Cease    CHA         GA   

        birthCountry   W  GS   G  SV   ER   SO  BB   ERA  BAOpp  WP  HR  gmLI  \
0     United Kingdom  17  25  29   0   91   60  73  3.49    NaN   3  10  1.00   
1     United Kingdom  13  22  30   0   96   66  86  4.13    NaN   8  11  1.00   
2     United Kingdom  16  34  39   1  124  103  91  3.53    NaN   2  14  1.00   
3                USA  21  37  42   1  114  108  82  2.99    NaN   8  11  1.00   
4                USA  13  27  29   0   79   53  72  3.07    NaN   6  11  1.00   
...              ...  ..  ..  ..  ..  ...  ...  ..   ...    ...  ..  ..   ...   
8733          Mexico  20  32  32   0   61  195  38  2.96  0.219   2  19   NaN   
8734             USA  10  30  32   0  103  146  56  5.15  0.278   9  38  0.55   
8735             USA  11  28  28   0   45  234  34  2.43  0.201   5   7   NaN   
8736             USA  14  31  31   0   72  125  40  3.61  0.268   2  19   NaN   
8737             USA  13  32  32   0   72  226  68  3.91  0.223  13  20   NaN   

      WAR  
0     3.6  
1     2.7  
2     3.2  
3     7.3  
4     4.8  
...   ...  
8733  4.4  
8734 -0.1  
8735  5.6  
8736  3.5  
8737  2.9  

[8738 rows x 20 columns]

In [21]:
corrMatrix = pitching_full_advanced_final.corr()
px.imshow(corrMatrix, text_auto=True, aspect='auto', zmax=1, zmin=-1, color_continuous_scale=px.colors.diverging.Fall)

In [22]:
from sklearn.preprocessing import StandardScaler

In [23]:
batting_heavy_advanced_main = batting_heavy_advanced_final.iloc[:,7:25]
batting_heavy_advanced_main

G   AB   R    H  2B  3B  HR   RBI    SB   CS  BB     SO   HBP    SH  \
0      117  439  65  118  18   7   4  92.0  25.0  NaN  27   24.0   4.0   2.0   
1      138  576  90  190  46   7   8  99.0  35.0  NaN  24   21.0   3.0   4.0   
2      126  524  60  149  29   6   4  85.0  15.0  NaN  21    9.0   3.0   3.0   
3      138  550  65  156  34   8   2  78.0  16.0  NaN  23   39.0   0.0   4.0   
4      143  558  62  155  27  12   3  82.0  20.0  NaN  23   37.0   6.0  11.0   
...    ...  ...  ..  ...  ..  ..  ..   ...   ...  ...  ..    ...   ...   ...   
12251  157  557  75  147  24   3  18  72.0   8.0  0.0  80  162.0   2.0   0.0   
12252  152  571  85  166  32   1  18  73.0   0.0  0.0  46  106.0  27.0   0.0   
12253  134  508  84  127  35   3  20  60.0   1.0  0.0  61  110.0   9.0   0.0   
12254  144  521  89  135  33   0  31  96.0   1.0  2.0  44  130.0   1.0   0.0   
12255  149  542  79  144  31   4  18  65.0   2.0  1.0  57  152.0  11.0   1.0   

        SF  WAR  oWAR  dWAR  
0      NaN  0.6   0.4  -0.2  
1      NaN  4.4   4.3  -0.2  
2      NaN  0.9   1.3  -0.6  
3      NaN  3.3   2.5   0.4  
4      NaN  3.2   2.8  -0.3  
...    ...  ...   ...   ...  
12251  3.0  2.4   2.6  -1.1  
12252  6.0  4.3   4.1  -0.5  
12253  7.0  4.9   3.2   2.1  
12254  6.0  2.3   2.3  -0.5  
12255  8.0  3.3   3.2  -0.2  

[12256 rows x 18 columns]

In [24]:
batting_heavy_advanced_main = batting_heavy_advanced_main.fillna(value = 0,axis=0)
batting_heavy_advanced_main

G   AB   R    H  2B  3B  HR   RBI    SB   CS  BB     SO   HBP    SH  \
0      117  439  65  118  18   7   4  92.0  25.0  0.0  27   24.0   4.0   2.0   
1      138  576  90  190  46   7   8  99.0  35.0  0.0  24   21.0   3.0   4.0   
2      126  524  60  149  29   6   4  85.0  15.0  0.0  21    9.0   3.0   3.0   
3      138  550  65  156  34   8   2  78.0  16.0  0.0  23   39.0   0.0   4.0   
4      143  558  62  155  27  12   3  82.0  20.0  0.0  23   37.0   6.0  11.0   
...    ...  ...  ..  ...  ..  ..  ..   ...   ...  ...  ..    ...   ...   ...   
12251  157  557  75  147  24   3  18  72.0   8.0  0.0  80  162.0   2.0   0.0   
12252  152  571  85  166  32   1  18  73.0   0.0  0.0  46  106.0  27.0   0.0   
12253  134  508  84  127  35   3  20  60.0   1.0  0.0  61  110.0   9.0   0.0   
12254  144  521  89  135  33   0  31  96.0   1.0  2.0  44  130.0   1.0   0.0   
12255  149  542  79  144  31   4  18  65.0   2.0  1.0  57  152.0  11.0   1.0   

        SF  WAR  oWAR  dWAR  
0      0.0  0.6   0.4  -0.2  
1      0.0  4.4   4.3  -0.2  
2      0.0  0.9   1.3  -0.6  
3      0.0  3.3   2.5   0.4  
4      0.0  3.2   2.8  -0.3  
...    ...  ...   ...   ...  
12251  3.0  2.4   2.6  -1.1  
12252  6.0  4.3   4.1  -0.5  
12253  7.0  4.9   3.2   2.1  
12254  6.0  2.3   2.3  -0.5  
12255  8.0  3.3   3.2  -0.2  

[12256 rows x 18 columns]

In [25]:
scaler = StandardScaler()
batting_heavy_advanced_main_scale = pd.DataFrame(scaler.fit_transform(batting_heavy_advanced_main),columns=['G','AB', 'R', 'H', '2B', '3B', 'HR', 'RBI', 'SB', 'CS', 'BB', 'SO', 'HBP', 'SH', 'SF', 'WAR', 'oWAR', 'dWAR'])
batting_heavy_advanced_main_scale.describe()

G            AB             R             H            2B  \
count  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04   
mean  -6.098980e-16  5.600394e-16 -3.061085e-16 -6.957011e-18  5.565609e-17   
std    1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00   
min   -6.195505e+00 -5.361025e+00 -2.815868e+00 -4.097632e+00 -2.713199e+00   
25%   -4.682473e-01 -5.725492e-01 -7.011651e-01 -6.360881e-01 -7.422680e-01   
50%    2.317508e-01  8.107063e-02 -7.636654e-02 -2.942582e-02 -4.664538e-02   
75%    6.772042e-01  6.920631e-01  6.445549e-01  6.486085e-01  6.489772e-01   
max    1.440839e+00  2.624504e+00  4.777838e+00  4.003094e+00  4.706776e+00   

                 3B            HR           RBI            SB            CS  \
count  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04   
mean   3.710406e-17  5.565609e-17  1.391402e-16 -6.493210e-17  6.029410e-17   
std    1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00   
min   -1.274061e+00 -1.237173e+00 -2.389256e+00 -9.563396e-01 -9.079894e-01   
25%   -7.774752e-01 -8.840822e-01 -7.437895e-01 -7.259217e-01 -9.079894e-01   
50%   -2.808894e-01 -1.778997e-01 -7.776737e-02 -3.418918e-01 -2.800632e-01   
75%    4.639892e-01  6.165557e-01  6.666103e-01  4.261678e-01  5.571718e-01   
max    7.664483e+00  5.206742e+00  4.701921e+00  9.028436e+00  7.882978e+00   

                 BB            SO           HBP            SH            SF  \
count  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04  1.225600e+04   
mean  -1.669683e-16 -2.226244e-16  1.855203e-17  3.710406e-17  1.113122e-16   
std    1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00  1.000041e+00   
min   -2.119339e+00 -1.906789e+00 -1.095839e+00 -8.464502e-01 -9.836510e-01   
25%   -7.347114e-01 -7.759837e-01 -5.518917e-01 -7.181469e-01 -9.836510e-01   
50%   -1.289368e-01 -1.416297e-01 -2.799180e-01 -3.332369e-01 -6.194175e-03   
75%    5.633770e-01  6.306274e-01  2.640292e-01  4.365831e-01  6.454437e-01   
max    7.702863e+00  4.243687e+00  1.250284e+01  7.749873e+00  5.206909e+00   

                WAR          oWAR          dWAR  
count  1.225600e+04  1.225600e+04  12256.000000  
mean  -1.321832e-16 -2.052318e-16      0.000000  
std    1.000041e+00  1.000041e+00      1.000041  
min   -3.167905e+00 -3.076999e+00     -4.605330  
25%   -7.075366e-01 -6.800278e-01     -0.682819  
50%   -6.966330e-02 -1.190346e-01     -0.072651  
75%    6.137723e-01  5.949567e-01      0.624684  
max    5.078885e+00  4.827905e+00      4.634362

In [26]:
from sklearn.cluster import KMeans

In [27]:
import plotly.graph_objects as go
inertia = []
for i in range(1,11):
    kmeans = KMeans(
        n_clusters=i, init="k-means++",
        n_init=10,
        tol=1e-04, random_state=42
    )
    kmeans.fit(batting_heavy_advanced_main_scale)
    inertia.append(kmeans.inertia_)

In [28]:
fig = go.Figure(data=go.Scatter(x=np.arange(1,11),y=inertia))
fig.update_layout(title="Inertia vs Cluster Number",xaxis=dict(range=[0,11],title="Cluster Number"),
                  yaxis={'title':'Inertia'},
                 annotations=[
        dict(
            x=3,
            y=inertia[2],
            xref="x",
            yref="y",
            text="Elbow!",
            showarrow=True,
            arrowhead=7,
            ax=20,
            ay=-40
        )
    ])

In [29]:
kmeans = KMeans(
        n_clusters= 4, init="k-means++",
        n_init=10,
        tol=1e-04, random_state=42
    )

In [30]:
kmeans.fit(batting_heavy_advanced_main_scale)
batting_heavy_advanced_main_scale['label']=kmeans.labels_
polar=batting_heavy_advanced_main_scale.groupby("label").mean().reset_index()
polar=pd.melt(polar,id_vars=["label"])
fig4 = px.line_polar(polar, r="value", theta="variable", color="label", line_close=True,height=800,width=1200)
fig4.show()

C:\Users\irvin\PycharmProjects\BaseballDashboard\venv\lib\site-packages\plotly\express\_core.py:271: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\irvin\PycharmProjects\BaseballDashboard\venv\lib\site-packages\plotly\express\_core.py:271: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\irvin\PycharmProjects\BaseballDashboard\venv\lib\site-packages\plotly\express\_core.py:271: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\irvin\PycharmProjects\BaseballDashboard\venv\lib\site-packages\plotly\express\_core.py:271: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [31]:
pie=batting_heavy_advanced_main_scale.groupby('label').size().reset_index()
pie.columns=['label','value']
px.pie(pie,values='value',names='label')

In [32]:
batting_heavy_advanced_main_scale.drop('label',axis = 1)

G        AB         R         H        2B        3B        HR  \
0     -1.613699 -1.311424 -0.605042 -1.135692 -0.974142  0.463989 -0.884082   
1     -0.277339  0.635227  0.596493  1.433701  2.272097  0.463989 -0.530991   
2     -1.040973 -0.103648 -0.845349 -0.029426  0.301166  0.215696 -0.884082   
3     -0.277339  0.265789 -0.605042  0.220376  0.880851  0.712282 -1.060628   
4      0.040842  0.379462 -0.749227  0.184690  0.069292  1.705454 -0.972355   
...         ...       ...       ...       ...       ...       ...       ...   
12251  0.931749  0.365253 -0.124428 -0.100798 -0.278520 -0.529182  0.351737   
12252  0.613568  0.564181  0.356186  0.577236  0.648977 -1.025768  0.351737   
12253 -0.531884 -0.330994  0.308125 -0.814518  0.996788 -0.529182  0.528283   
12254  0.104478 -0.146275  0.548432 -0.529030  0.764914 -1.274061  1.499284   
12255  0.422659  0.152116  0.067818 -0.207856  0.533040 -0.280889  0.351737   

            RBI        SB        CS        BB        SO       HBP        SH  \
0      0.823321  0.963810 -0.907989 -1.167407 -1.244854 -0.007944 -0.589844   
1      1.097566  1.731869 -0.907989 -1.297216 -1.327596 -0.279918 -0.333237   
2      0.549077  0.195750 -0.907989 -1.427025 -1.658563 -0.279918 -0.461540   
3      0.274833  0.272556 -0.907989 -1.340486 -0.831145 -1.095839 -0.333237   
4      0.431544  0.579780 -0.907989 -1.340486 -0.886306  0.536003  0.564886   
...         ...       ...       ...       ...       ...       ...       ...   
12251  0.039766 -0.341892 -0.907989  1.125882  2.561270 -0.551892 -0.846450   
12252  0.078944 -0.956340 -0.907989 -0.345285  1.016756  6.247450 -0.846450   
12253 -0.430367 -0.879534 -0.907989  0.303759  1.127078  1.351924 -0.846450   
12254  0.980033 -0.879534 -0.489372 -0.431824  1.678691 -0.823865 -0.846450   
12255 -0.234478 -0.802728 -0.698681  0.130681  2.285464  1.895871 -0.718147   

             SF       WAR      oWAR      dWAR  
0     -0.983651 -1.117598 -1.292020 -0.246985  
1     -0.983651  0.613772  0.696955 -0.246985  
2     -0.983651 -0.980911 -0.833026 -0.595652  
3     -0.983651  0.112586 -0.221033  0.276017  
4     -0.983651  0.067024 -0.068035 -0.334152  
...         ...       ...       ...       ...  
12251 -0.006194 -0.297475 -0.170034 -1.031487  
12252  0.971263  0.568210  0.594957 -0.508486  
12253  1.297082  0.841584  0.135962  1.757854  
12254  0.971263 -0.343038 -0.323032 -0.508486  
12255  1.622901  0.112586  0.135962 -0.246985  

[12256 rows x 18 columns]

In [35]:
from sklearn.decomposition import PCA
# import seaborn as sn
pca_num_components = 2

reduced_data = PCA(n_components=pca_num_components).fit_transform(batting_heavy_advanced_main_scale.drop('label',axis = 1))
results = pd.DataFrame(reduced_data,columns=['pca1','pca2'])

In [36]:
px.scatter(results,x="pca1", y="pca2", color=batting_heavy_advanced_main_scale['label'],hover_name=batting_heavy_advanced_final['fullName'])

In [37]:
from sklearn.cluster import DBSCAN
cluster = DBSCAN(eps=5, min_samples=2).fit(batting_heavy_advanced_main_scale)
batting_heavy_advanced_main_scale['label'] = cluster.labels_
batting_heavy_advanced_main_scale

G        AB         R         H        2B        3B        HR  \
0     -1.613699 -1.311424 -0.605042 -1.135692 -0.974142  0.463989 -0.884082   
1     -0.277339  0.635227  0.596493  1.433701  2.272097  0.463989 -0.530991   
2     -1.040973 -0.103648 -0.845349 -0.029426  0.301166  0.215696 -0.884082   
3     -0.277339  0.265789 -0.605042  0.220376  0.880851  0.712282 -1.060628   
4      0.040842  0.379462 -0.749227  0.184690  0.069292  1.705454 -0.972355   
...         ...       ...       ...       ...       ...       ...       ...   
12251  0.931749  0.365253 -0.124428 -0.100798 -0.278520 -0.529182  0.351737   
12252  0.613568  0.564181  0.356186  0.577236  0.648977 -1.025768  0.351737   
12253 -0.531884 -0.330994  0.308125 -0.814518  0.996788 -0.529182  0.528283   
12254  0.104478 -0.146275  0.548432 -0.529030  0.764914 -1.274061  1.499284   
12255  0.422659  0.152116  0.067818 -0.207856  0.533040 -0.280889  0.351737   

            RBI        SB        CS        BB        SO       HBP        SH  \
0      0.823321  0.963810 -0.907989 -1.167407 -1.244854 -0.007944 -0.589844   
1      1.097566  1.731869 -0.907989 -1.297216 -1.327596 -0.279918 -0.333237   
2      0.549077  0.195750 -0.907989 -1.427025 -1.658563 -0.279918 -0.461540   
3      0.274833  0.272556 -0.907989 -1.340486 -0.831145 -1.095839 -0.333237   
4      0.431544  0.579780 -0.907989 -1.340486 -0.886306  0.536003  0.564886   
...         ...       ...       ...       ...       ...       ...       ...   
12251  0.039766 -0.341892 -0.907989  1.125882  2.561270 -0.551892 -0.846450   
12252  0.078944 -0.956340 -0.907989 -0.345285  1.016756  6.247450 -0.846450   
12253 -0.430367 -0.879534 -0.907989  0.303759  1.127078  1.351924 -0.846450   
12254  0.980033 -0.879534 -0.489372 -0.431824  1.678691 -0.823865 -0.846450   
12255 -0.234478 -0.802728 -0.698681  0.130681  2.285464  1.895871 -0.718147   

             SF       WAR      oWAR      dWAR  label  
0     -0.983651 -1.117598 -1.292020 -0.246985      0  
1     -0.983651  0.613772  0.696955 -0.246985      0  
2     -0.983651 -0.980911 -0.833026 -0.595652      0  
3     -0.983651  0.112586 -0.221033  0.276017      0  
4     -0.983651  0.067024 -0.068035 -0.334152      0  
...         ...       ...       ...       ...    ...  
12251 -0.006194 -0.297475 -0.170034 -1.031487      0  
12252  0.971263  0.568210  0.594957 -0.508486      0  
12253  1.297082  0.841584  0.135962  1.757854      0  
12254  0.971263 -0.343038 -0.323032 -0.508486      0  
12255  1.622901  0.112586  0.135962 -0.246985      0  

[12256 rows x 19 columns]

In [38]:
pca_num_components = 2

reduced_data = PCA(n_components=pca_num_components).fit_transform(batting_heavy_advanced_main_scale.drop('label',axis = 1))
results = pd.DataFrame(reduced_data,columns=['pca1','pca2'])

In [39]:
px.scatter(results,x="pca1", y="pca2", color=batting_heavy_advanced_main_scale['label'],hover_name=batting_heavy_advanced_final['fullName'])

Pitch


In [40]:
pca_num_components = 2

reduced_data = PCA(n_components=pca_num_components).fit_transform(batting_heavy_advanced_main_scale.drop('label',axis = 1))
results = pd.DataFrame(reduced_data,columns=['pca1','pca2'])

In [41]:
px.scatter(results,x="pca1", y="pca2", color=batting_heavy_advanced_main_scale['label'],hover_name=batting_heavy_advanced_final['fullName'])

Pitch